 Text to Audio + Image Slideshow Video Generator
This notebook takes any input text Hindi or English, converts it to audio using gTTS,
and creates a slideshow video using your images with that voiceover.


In [58]:
!pip install gTTS moviepy


 Step 2: Upload Your Image Files
Upload 10–20 `.jpg` or `.png` images. These will be used as slideshow background scenes. After running this code, you will get the option of choose file, you can select multiple images by clicking on it.


In [64]:
from google.colab import files
import os

os.makedirs("images", exist_ok=True)
uploaded = files.upload()

# Move uploaded files to images/ folder
for name in uploaded.keys():
    os.rename(name, os.path.join("images", name))


Saving prisoner-writing-letter-their-cell-expressing-emotions-through-handwritten-words-paper_1314467-129921.avif to prisoner-writing-letter-their-cell-expressing-emotions-through-handwritten-words-paper_1314467-129921.avif
Saving 9271b915-8ae2-5eeb-a2d6-03909b2f9d95.jpg to 9271b915-8ae2-5eeb-a2d6-03909b2f9d95.jpg
Saving 6902cc50-077a-54c0-8724-d2833af51199.jpg to 6902cc50-077a-54c0-8724-d2833af51199.jpg
Saving posters-vintage-handwritten-letter.jpg to posters-vintage-handwritten-letter.jpg
Saving senior-woman-relaxing-chair-reading-letter-23960703.webp to senior-woman-relaxing-chair-reading-letter-23960703.webp
Saving c9abaa67-29fb-5b0f-bc50-e955754c47b5.jpg to c9abaa67-29fb-5b0f-bc50-e955754c47b5.jpg
Saving 3bd0d029-c291-4172-8c67-5a6c9527734a.png to 3bd0d029-c291-4172-8c67-5a6c9527734a.png
Saving d59079c1-885d-490d-8cc7-682b189c11ea.png to d59079c1-885d-490d-8cc7-682b189c11ea.png


 Step 3: Define Function to Convert Text ➜ Audio ➜ Video
This function does:
- Converts text to speech
- Loads images
- Assigns duration per image
- Creates slideshow
- Overlays the audio
- Exports the final video


In [65]:
from gtts import gTTS
from moviepy.editor import *
import os
import uuid

def text_to_video_with_images(text, image_folder='images', language='hi'):
    # Step 1: Convert Text to Audio
    audio_path = f"audio_{uuid.uuid4()}.mp3"
    tts = gTTS(text=text, lang=language)
    tts.save(audio_path)

    # Step 2: Load Audio & Duration
    audio_clip = AudioFileClip(audio_path)
    duration = audio_clip.duration

    # Step 3: Load All Images from Folder
    image_files = sorted([
        os.path.join(image_folder, img)
        for img in os.listdir(image_folder)
        if img.endswith(('.jpg', '.jpeg', '.png'))
    ])

    if len(image_files) == 0:
        raise Exception("❌ No images found in folder!")

    duration_per_image = duration / len(image_files)

    image_clips = [
        ImageClip(img).set_duration(duration_per_image).resize(height=720)
        for img in image_files
    ]

    # Step 4: Make Video from Image Clips
    video_clip = concatenate_videoclips(image_clips, method="compose")
    final_video = video_clip.set_audio(audio_clip)

    # Step 5: Export Video
    output_path = f"video_output_{uuid.uuid4()}.mp4"
    final_video.write_videofile(output_path, fps=24)

    return output_path


 Step 4: Define a Helper to Display the Video Inside Colab
This will embed the final `.mp4` video and force reload by using a unique ID.


In [66]:
from IPython.display import HTML
from base64 import b64encode
import uuid

def show_video(filename):
    with open(filename, 'rb') as f:
        mp4 = f.read()
    data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
    unique_id = uuid.uuid4()
    return HTML(f"""
    <video id="{unique_id}" width=640 height=360 controls autoplay>
        <source src="{data_url}" type="video/mp4">
    </video>
    """)


 Step 5: Input Your Story/Text and Generate the Final Video
Enter your Hindi or English story below.
The function will generate audio + slideshow video.
 Download Final MP4 Video (Optional)
This will download the generated video to your local device.



In [67]:
text =  "अन हर दिन की तरह सुबह सुबह अपनी साइकिल उठाकर डाकघर पहुंचा। गाँव छोटा था इसलिए चिट्ठियाँ भी कम आती थीं लेकिन एक चिट्ठी थी जो पिछले पाँच सालों से हर महीने आती थी  दादी माँ के नाम हर महीने जब वह दादी माँ को चिट्ठी देता वे खुशी से मुस्करातीं और उसे आशीर्वाद देतीं लेकिन कभी भी उन्होंने किसी को वो चिट्ठी पढ़ने नहीं दी एक दिन अनायास ही दादी माँ का देहांत हो गया पूरा गाँव शोक में डूबा अगले दिन जब डाकघर में वही चिट्ठी फिर आई तो अनय का मन विचलित हो गया अब ये चिट्ठी किसे दूँ उसने बुदबुदाया वह चिट्ठी लेकर दादी माँ के घर गया जहाँ उनकी पोती गौरी आई हुई थी गौरी अनय की बचपन की दोस्त थी लेकिन शहर जाकर पढ़ाई और नौकरी में लग गई थी अनय ने चिट्ठी उसे पकड़ा दी और कहा शायद अब इसे पढ़ने का समय आ गया है गौरी ने चिट्ठी खोली और पढ़ना शुरू किया उसमें लिखा था प्रिय माँ मैं जानता हूँ मैंने तुमसे बहुत दूरियाँ बना ली हैं पर तुम्हारा बेटा हर दिन तुम्हें याद करता है इस जेल की चारदीवारी मुझे रोक सकती है, पर मेरी भावनाओं को नहीं। हर महीने ये चिट्ठी भेजता हूँ ताकि तुम जान सको, मैं अब भी तुम्हें उतना ही चाहता हूँ। एक दिन ज़रूर लौटूंगा माँ... तब तक, माफ कर देना। तुम्हारा बेटा राजू गौरी की आँखें भर आईं। अनय चौंक गया। दादी माँ का बेटा... जेल में? गौरी ने सिर हिलाया, हाँ, वो कभी किसी से नहीं बोलीं। उनके लिए ये चिट्ठियाँ जीने का सहारा थीं। अनय ने एक नज़र गौरी की ओर देखा। वर्षों से दिल में छुपा प्यार आज खुद-ब-खुद शब्दों में बदल गया। गौरी, क्या मैं भी एक चिट्ठी तुम्हारे लिए लिख सकता हूँ? गौरी मुस्कराई और कहा, अब चिट्ठी की ज़रूरत नहीं, अनय। मैं यहीं हूँ। सीख: हर भावना को कहने के लिए कभी-कभी शब्दों की नहीं, दिल की ज़रूरत होती है। और इंतज़ार की चिट्ठियाँ भी कभी मंज़िल तक पहुँच ही जाती हैं।."


video_file = text_to_video_with_images(text)
show_video(video_file)


Moviepy - Building video video_output_3e3b85a8-d148-4b65-b72b-e0f3345b5acf.mp4.
MoviePy - Writing audio in video_output_3e3b85a8-d148-4b65-b72b-e0f3345b5acfTEMP_MPY_wvf_snd.mp3


MoviePy - Done.
Moviepy - Writing video video_output_3e3b85a8-d148-4b65-b72b-e0f3345b5acf.mp4



Moviepy - Done !
Moviepy - video ready video_output_3e3b85a8-d148-4b65-b72b-e0f3345b5acf.mp4
